In [ ]:
import numpy as np
from itertools import permutations
import random


In [7]:
eta = 0.05

In [9]:
## Agents' Initialization
## 5 agents in total, no sex distinction, true values 
N = 6     # Number of Agents 
v = [9, 9, 8, 8, 6, 6]

epsilon_0 = 0.5 # initial probability of exploration
K = np.zeros(N)

# Mean and std deviation of the noise signals (sampled form a std Normal )
noise_mean = 0 
noise_std = 0.5

In [10]:
## Initialization prior beliefs matrix 
np.random.seed(25)
Q = np.random.uniform(5, 10, size=(N, N))
np.fill_diagonal(Q, -1e7)    # On the diagonal negative rewards - to avois self pairing 

In [11]:
## Initialization prior beliefs of being accepted probailities matrix
np.random.seed(25)
p = np.random.uniform(0, 1, size=(N, N))
np.fill_diagonal(p, 1)    # On the diagonal probablity one of having ngative reward  

In [12]:
## Initialization prior beliefs of being askec out probailities matrix
np.random.seed(25)
c = np.random.uniform(0, 1, size=(N, N))
np.fill_diagonal(c, 1)    # On the diagonal probablity one of having ngative reward  

## 1.1 Sequential offers Simulation

- we take the agent's to take in turn the decision, this can be modified TBD

In [13]:
## For the sequential setting, we need tokeep track for each agent,
## wich other agents have asked it out so far, stored in a dictionary S
S = {key: [] for key in range(N)}

In [14]:
def greedy_proposal(i, Q = Q, p = p):
    '''This function returns the the index of agents to propose 
    under the greedy approach, for agent i '''

    q = np.array(Q[i])
    p_i = np.array(p[i])

    return np.argmax(p_i*q)

In [15]:
def relevant_probabilities(k, i, S_prime, c = c):
    ' This function defines the relevant probabilities as defined in (8)'
    S_prime = list(S_prime)  # Ensure S_prime is a list for indexing
    all_perms = list(permutations(S_prime))
    sum_probs = 0
    
    for T in all_perms:
        product = 1
        # Find the position of k in the permutation
        k_index = T.index(k)
        # Compute the product for all j preceding k in T
        for j_index in range(k_index):
            j = T[j_index]
            if j != i and k != i:  # Exclude diagonal elements for i
                product *= (1 - c[j][i]) * c[k][i]
        
        sum_probs += product / len(S_prime)
    
    return sum_probs / len(all_perms)

In [16]:
def acceptance_offer_sequential(i, h,  Q = Q, c = c , S = S ):

    '''This function defines the acceptance probability of agent i,
    when asked out by agent h, in the sequential setitng'''

    S[i].append(h)

    S_prime = list(set([i for i in range(N)]) - set(S[i]))
    sum_rel_prob = 0

    for k in S_prime: 
        sum_rel_prob += relevant_probabilities(k, i, S_prime) * Q[i, k] ### check this value 

    if Q[i, h] > sum_rel_prob: 
        return 1     ## The offer has been accepted 
    else: 
        return 0     ## The offer has been rejected
    

In [17]:

T = 100 ## Time steps


for t in range(T): 

    epsilon = epsilon_0**(t/1000)
    ## in turn one of the agents make the proposal 
    i  = t % N 
    ## Agent i makes the proposal with epsilong greedy algorithm 
    if random.random() < epsilon:
        # Exploration: with probability epsilon
        #print(list(range(N)).remove(i))

        j = random.choice(list(range(N)))
    else:
        # Greedy: with the remaining probability (1 - epsilon)

        j = greedy_proposal(i)

    ## Evaluation of acceptance of the proposal 

    accepted = acceptance_offer_sequential(i = j, h = i)
        
    
    ## Update of the probabilities 
    
    # Agent perspective  - Accepted offer
    p[i, j] = (1-eta)*p[i, j] + eta * accepted

    # Arm perspective - Offer recieved 
    
    c[j, i] = (1-eta)*c[i, j] + eta 

    ## should we update also if the offer has not been made - ? 

In [19]:
def invert_offers(offers):
    ' function to invert the offers being made '
    inverted_offers = {}
    for proposer, recipient in offers.items():
        inverted_offers.setdefault(recipient, []).append(proposer)
    return inverted_offers



In [21]:
def greedy_decision(i, offers, Q=Q, p = p):
    'Function that decides wich to accept the offer to greedy decision'

    q = np.array(Q[i, offers])
    #p_i = np.array(p[i, offers])

    return offers[np.argmax(q)]

## 1.2 Simulation - Simoultaneous offers


In [22]:
T = 100000
epsilon_0 = 0.01
eta = 0.05
## Agents' Initialization
## 5 agents in total, no sex distinction, true values 
N = 6     # Number of Agents 

epsilon_0 = 0.5 # initial probability of exploration
K = np.zeros(N)

# Mean and std deviation of the noise signals (sampled form a std Normal )
noise_mean = 0 
noise_std = 0.5

In [28]:
v = np.random.uniform(0, 0.99, (6,6))
N = 6       # Number of Agents 
np.fill_diagonal(v, 0)

v[0,1] = 1
v[1,0] = 1

v[2, 3] = 1
v[3,2] = 1

v[4,5] = 1
v[5,4] = 1


In [29]:
for t in range(T): 

    ## Each agent does offers 

    offers = {}
    epsilon = epsilon_0**(t/1000)

    for i in range(N):
        if random.random() < epsilon:
        # Exploration: with probability epsilon
            offers[i] = random.choice(list(range(N)))
        else:
        # Greedy: with the remaining probability (1 - epsilon)
            offers[i] = greedy_proposal(i)
        

    #print('Offers \n')

    # print(offers)


    ## Each agent that recieved the offer - decides wheter to accept
    ## they do the greedy decision  
        
    offers_recievers = invert_offers(offers)

    #print('offers recievers \n')

    # print(offers_recievers)

    ## stores the matches 

    m = {}

    for j in offers_recievers.keys():
        m[j] = greedy_decision(j, offers_recievers[j])
        Q[m[j], j] =  Q[m[j], j]/2+  (v[j, m[j]] + np.random.normal(noise_mean, noise_std, 1))/2 ## Update the Q of the observed value - if matches take place
    
    print('matches \n')
    print(m)

    ## Update of the probabilities according to the decisions 

    for i in range(N):
        if i in m.items(): 
            k = next((key for key, value in m.items() if value == i), None)
            p[i, k] = (1-eta)*p[i, k] + eta 
        else:
            k = offers[i]  # who they offered 
            p[i, k] = (1-eta)*p[i, k] 

        
       ## No need to update the probability of being chosen in this setting  

        #if i in m.keys(): 
        #   k = m[i]   
        #   c[i, k] = (1-eta)*c[i, k] + eta 
        # else:
        #    c[i, k] = (1-eta)*c[i, k] + eta    

matches 

{1: 4, 5: 1, 2: 3, 0: 5}
matches 

{0: 0, 1: 3, 3: 2, 2: 5}
matches 

{4: 0, 2: 1, 0: 5, 5: 4}
matches 

{1: 5, 2: 1, 4: 2, 5: 4}
matches 

{0: 1, 3: 2, 2: 3, 4: 5}
matches 

{5: 0, 1: 1, 4: 2, 2: 3, 3: 5}
matches 

{5: 1, 2: 2, 0: 3, 4: 4, 1: 5}
matches 

{1: 0, 3: 1, 5: 2, 2: 5}
matches 

{5: 3, 3: 2}
matches 

{0: 0, 3: 1, 1: 2, 2: 3}
matches 

{4: 0, 0: 1, 2: 3, 3: 4}
matches 

{5: 0, 3: 1, 1: 2, 4: 3, 2: 4, 0: 5}
matches 

{0: 3, 3: 1, 5: 2}
matches 

{3: 0, 5: 2, 2: 3, 1: 4, 4: 5}
matches 

{4: 3, 5: 4, 3: 5}
matches 

{1: 0, 0: 1, 2: 2, 4: 3, 5: 5}
matches 

{1: 0, 4: 2, 2: 4, 5: 5}
matches 

{5: 0, 2: 1, 1: 2, 0: 4}
matches 

{1: 0, 0: 1, 2: 4}
matches 

{4: 2, 0: 1, 2: 4, 5: 5}
matches 

{0: 0, 3: 1, 5: 2, 4: 4, 1: 5}
matches 

{0: 5, 2: 1, 3: 4}
matches 

{0: 1, 2: 4, 3: 3, 4: 5}
matches 

{5: 4, 4: 1, 2: 2, 0: 3, 1: 5}
matches 

{5: 0, 0: 1, 4: 2, 1: 3, 2: 5}
matches 

{0: 5, 3: 1, 1: 2, 4: 3}
matches 

{1: 0, 5: 1, 4: 2, 2: 4}
matches 

{5: 0, 2: 1, 1: 4, 0: 3}
ma